<a href="https://colab.research.google.com/github/MarioCastilloM/Activos_Derivados/blob/main/Tarea_Portafolio.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<img style="float: right;" align="center" src="https://www.udp.cl/cms/wp-content/uploads/2021/06/UDP_LogoRGB_2lineas_Color_SinFondo.png">

# Tarea Portafolio

<!-- ![picture](https://www.udp.cl/cms/wp-content/uploads/2021/06/UDP_LogoRGB_2lineas_Color_SinFondo.png) -->

## Integrantes

-  Mario Castillo
-  Felipe Gálvez

En el presente trabajo, se pide crear una función que nos permita automatizar el análisis de portafolios y de la frontera eficiente. Para esto, se desarrolló una clase de objeto en Python que incluye métodos que permiten llevar a cabo el análisis solicitado. A continuación se detallan cada uno de los métodos de la clase y cómo se hacen cargo de lo indicado en el enunciado de este trabajo.

## Clase Portfolio

Esta instancia genera un portafolio que toma como argumentos lo siguiente:

- df: un set de datos con la primera variable nombrada como ***Date*** y con las variables restantes con el nombre del **Symbol** de la acción y como valor su precio. Este input es opcional y de no ingresarlo, se debe ingresar el siguiente argumento, **ticker**

- ticker: una lista con los **Symbols** de las acciones con las que se quiere trabajar (los nombres de las acciones deben coincidir con los de [yahoo finance](https://finance.yahoo.com/)). Si fue provisto el argumento df, entonces el programa no tomará en cuenta el argumento ticker.

- start: un string que provee la fecha de inicio de historia de los datos. Debe tener el formato YYYY-mm-dd. Por defecto, comienza el 2010-01-01.

- end: un string que provee la fecha de fin de historia de los datos. Debe tener el formato YYYY-mm-dd. Por defecto finaliza en el día actual.

- rf: es un float que indica la tasa libre de riesgo. Por defecto toma el valor 0.05.

- J: es un entero que indica el número de simulaciones de portafolios que llevará a cabo el programa. Por defecto, el número es 10.000.

Para la extracción de datos de la web (opcional) debemos instalar la librería ***yfinance*** con el comando a continuación:

In [1]:
!pip install yfinance

     |████████████████████████████████| 6.3 MB 11.0 MB/s 
  Attempting uninstall: lxml
    Found existing installation: lxml 4.2.6
    Uninstalling lxml-4.2.6:
      Successfully uninstalled lxml-4.2.6


La clase Portfolio se crea en la siguiente celda

In [2]:
class Portfolio():

  from datetime import date
  def __init__(
      self,
      df = None, 
      ticker = None, 
      start = date(2010, 1, 1), 
      end = date.today(), 
      rf = 0.05, 
      J = 10000):
    self.df = df if df is not None else ticker
    self.start = start
    self.end = end
    self.rf = rf
    self.J = J
  
  def _prepare_data(self):
    import pandas as pd
    import yfinance as yf
    if isinstance(self.df, pd.DataFrame):
      self.df.iloc[:, 1:] = self.df.iloc[:, 1:].pct_change()
      df = self.df.dropna()
      df.set_index('Date', inplace = True)
    else:
      data = [yf.download(x, start=self.start, end=self.end, progress=False) for x in self.df]
      for i in range(len(data)):
        data[i]['ticker'] = self.df[i]
      df = pd.concat(data)
    df = (df.reset_index().pivot(index='Date',columns="ticker", values="Adj Close").sort_index(level=[1,0]))
    df = df.pct_change()
    df.dropna(inplace = True)
    return df
  
  def _portfolio_sim(self, df):
    import pandas as pd
    import numpy as np
    n = self.J
    m = len(df.columns)
    matrix = np.zeros((n, m))
    p_ret = np.zeros(n)
    p_risk = np.zeros(n)
    sharpe = np.zeros(n)
    cov = df.cov()
    avg_ret = df.apply(np.mean, axis = 0)
    for i in range(n):
      w = np.random.uniform(size = m)
      w = w/np.sum(w)
      matrix[i, :] = w
      ret = np.sum(w * avg_ret)
      ret = ((ret + 1)**252) - 1
      p_ret[i] = ret
      risk = (w.T@cov@w)**0.5
      p_risk[i] = risk
      s = (ret - self.rf) / risk
      sharpe[i] = s
    portfolio_values = pd.DataFrame({
        'Retorno': p_ret,
        'Riesgo': p_risk,
        'Sharpe Ratio': sharpe
    })
    matrix = pd.DataFrame(matrix, 
                          columns = df.columns)
    portfolio_values = pd.concat([portfolio_values.reset_index(drop=True), matrix], axis=1)
    min_var = portfolio_values[portfolio_values['Riesgo'] == np.min(portfolio_values['Riesgo'])]
    max_ret = portfolio_values[portfolio_values['Retorno'] == np.max(portfolio_values['Retorno'])]
    max_sharpe = portfolio_values[portfolio_values['Sharpe Ratio'] == np.max(portfolio_values['Sharpe Ratio'])]
    min_max = min_var.append(max_ret).append(max_sharpe).reset_index(drop = True).rename(index = {
        0: 'Min Var',
        1: 'Max Ret',
        2: 'Tangente'
        })
    return min_max, portfolio_values

  def efficient_frontier(self, df, min_max_df):
    import plotly.express as px
    import plotly.graph_objects as go
    fig = px.scatter(df, x = "Riesgo", y = "Retorno", color = "Sharpe Ratio", hover_data = ['Sharpe Ratio'],
                     color_continuous_scale=px.colors.sequential.Viridis,
                     title = "Efficient Frontier")
    fig.add_trace(go.Scatter(x = [min_max.loc['Tangente']['Riesgo']], 
                             y = [min_max.loc['Tangente']['Retorno']], 
                             mode = 'markers', name = 'Optimal Portfolio', 
                             marker = dict(size = [30], color = 'yellow')))
    fig.add_trace(go.Scatter(x = [min_max.loc['Min Var']['Riesgo']], 
                             y = [min_max.loc['Min Var']['Retorno']], 
                             mode = 'markers', name = 'Min Risk Portfolio', 
                             marker = dict(size = [30], color = 'navy')))
    fig.update_layout(coloraxis_colorbar = dict(
        title = 'Sharpe Ratio',
        thicknessmode = 'pixels', thickness = 25,
        lenmode = 'pixels',
        yanchor = 'middle', y = 0.4,
        dtick = 5
    ))
    return fig

  def investment_growth(self, df, weights):
    import plotly.express as px
    import numpy as np
    import pandas as pd
    ini_inv = 10000
    a = (weights.loc['Tangente'][3:] * df.iloc[1:]).apply(sum, axis = 1)
    x = np.zeros(len(a))
    for i in range(1, len(a)):
      x[0] = 10000
      x[i] = x[i-1] * (1+a[i-1])
    df_ = pd.DataFrame({"Date": a.index,
                        "Inversión": x})
    fig = px.line(df_, x = "Date", y = "Inversión",
                     title = "Investment Growth")
    return fig, df_
  
  def portfolio_composition(self, min_max):
    import pandas as pd
    import plotly.express as px
    x = input('Selecciona una opción ("Min Var", "Max Ret", "Tangente"): ')
    port = min_max.loc[x,:][3:]
    p = pd.DataFrame(port).sort_values(by = [x]).reset_index().rename(columns = {"index": "Stock"})
    p1 = px.bar(p, x="Stock", y=x, color="Stock", title= p.columns[1] + " Portfolio Composition")
    return p1

## Definición del Objeto Portfolio()

Se genera un objeto de clase Portfolio() con las siguientes características:

- tickers: Tesla, Amazon, Apple, S&P 500, SSE Composite Index, Ether (Ethereum), Banco Chile, Aurora Cannabis Inc.

- Número de simulaciones, J: 100.000

Los demás argumentos son tomados por defecto.

In [3]:
a = Portfolio(ticker=['TSLA', 'AMZN', 'AAPL', '^GSPC', '000001.SS', 'ETH-USD', 'CHILE.SN', 'ACB'], J = 100000)

### _prepare_data():

La función _prepare_data() realiza lo siguiente:

 - Carga las librerías pandas y yfinance
 - Evalúa si el argumento df fue entregado por el usuario o no
 - De encontrar el df dado por el usuario, entonces calcula los retornos y elimina los valores NaN
 - De no encontrar el argumento df (o encontrarlo vacío), entonces descarga los datos especificados en el argumento ticker y transforma el data set para finalmente obtener los retornos de cada acción.
 - Entrega un objeto Pandas Data Frame con la fecha y los retornos de cada acción. 

In [4]:
b = a._prepare_data()

In [5]:
b.head()

ticker      000001.SS      AAPL       ACB  ...   ETH-USD      TSLA     ^GSPC
Date                                       ...                              
2015-08-08   0.000000  0.000000  0.000000  ... -0.728250  0.000000  0.000000
2015-08-09   0.000000  0.000000  0.000000  ... -0.068268  0.000000  0.000000
2015-08-10   0.049199  0.036358  0.050000  ...  0.009333 -0.005649  0.012808
2015-08-11  -0.000129 -0.052038 -0.008658  ...  0.507323 -0.015634 -0.009557
2015-08-12  -0.010588  0.015420  0.039301  ...  0.140075  0.003370  0.000950

[5 rows x 8 columns]

### _portfolio_sim()

La función _portfolio_sim() se encarga de realizar la simulación de los J portafolios. Para esto, genera una matriz de ceros de J filas y m columnas, donde m representa el número de activos incorporados en el portafolio. Asimismo, genera tres vectores vacíos para almacenar el retorno, el riesgo y el ratio sharpe, además de la matriz de riesgo $\Sigma$ y el vector de retornos esperados (promedio) $\mu$. Luego, por cada iteración, se genera un vector de retornos aleatorios con una función de distirbución generadora de datos uniforme y se actualizan cada fila de la matriz (una por iteración) y lada posición de los vectores generados (una posición por iteración). Finalmente se consolidan la matriz y los vectores en un Pandas Data Frame y de este df se extrae uno con sólo tres filas que contiene los portafolios de mínima varianza, máximo retorno y máximo ratio sharpe o portafolio tangente. La función retorna ambos data frames.

In [6]:
min_max, simulation = a._portfolio_sim(b)

### efficient_frontier()

Para graficar la frontera eficiente, se crea el método efficient_frontier(), que, a través de plotly, grafica el data set que recibe de insumo (las J combinaciones simuladas de riesgo y retorno) y adicionalmente grafica los portafolios de mínima varianza y tangente.

In [7]:
a.efficient_frontier(simulation, min_max)

### investment_growth()

El método investment_growth calcula y grafica la evolución de una inversión en el portafolio tangente desde el inicio hasta el final de la muestra. Retorna tanto la figura en plotly, como el Pandas Data Frame. Para calcular la evolución de la inversión, se genera un vector de ceros que se irá actualizando de la siguiente manera:

- En la primera posición se actualiza con la inversión inicial de 10.000 USD
- Luego, por cada período hacia adelante, se multiplica el saldo anterior por (1 + $r_{t-1}$), donde $r_{t-1}$ es el retorno del portafolio tangente en el t anterior.

In [8]:
figura, data = a.investment_growth(b, min_max)

In [9]:
figura.show()

In [10]:
data.head()

Date     Inversión
0 2015-08-09  10000.000000
1 2015-08-10   9692.804299
2 2015-08-11   9770.725074
3 2015-08-12  11925.009225
4 2015-08-13  12713.115457

### portfolio_composition

Finalmente, se genera el método portfolio_composition() que permite graficar la composición del portafolio basado en el Pandas Data Frame con los portafolios de mínima varianza, máximo retorno y tangente generado por el método portfolio_sim().

A continuación, visualizaremos la composición de estos 3 portafolios:

In [11]:
# Ingresa Tangente al input solicitado en consola

a.portfolio_composition(min_max)

Selecciona una opción ("Min Var", "Max Ret", "Tangente"): Tangente


In [12]:
# Ingresa Min Var al input solicitado en consola

a.portfolio_composition(min_max)

Selecciona una opción ("Min Var", "Max Ret", "Tangente"): Min Var


In [13]:
# Ingresa Max Ret al input solicitado en consola

a.portfolio_composition(min_max)

Selecciona una opción ("Min Var", "Max Ret", "Tangente"): Max Ret
